# Gold Layer Analytics & Reporting

This notebook performs post-Gold exploration and reporting.

Purpose:
- validate dimensional model
- compute business KPIs
- perform exploratory analysis
- create reporting views for BI tools

Inputs:
- gold.dim_customers
- gold.dim_products
- gold.fact_sales

Outputs:
- gold.report_customers
- gold.report_products

Note:
This is analysis + semantic modeling, not data transformation.


In [0]:
from pyspark.sql import functions as F
from pyspark.sql.window import Window


## Step 1. Load Gold tables

In [0]:
spark.sql("USE CATALOG datawarehouse")

fact_df = spark.table("gold.fact_sales")
cust_df = spark.table("gold.dim_customers")
prod_df = spark.table("gold.dim_products")

fact_df.printSchema()

root
 |-- order_number: string (nullable = true)
 |-- product_key: integer (nullable = true)
 |-- customer_key: integer (nullable = true)
 |-- order_date: date (nullable = true)
 |-- ship_date: date (nullable = true)
 |-- due_date: date (nullable = true)
 |-- sales_amount: double (nullable = true)
 |-- quantity: integer (nullable = true)
 |-- price: double (nullable = true)



## Step 2. Database exploration
Basic metadata checks

In [0]:
spark.sql("""
SELECT *
FROM information_schema.tables
WHERE table_schema = 'gold'
""").display()

table_catalog table_schema table_name table_type is_insertable_into commit_action table_owner comment created created_by last_altered last_altered_by data_source_format storage_sub_directory storage_path datawarehouse gold report_customers MANAGED YES PRESERVE eshan.sharma108@gmail.com null 2026-02-08T16:03:16.369Z eshan.sharma108@gmail.com 2026-02-08T16:13:56.178Z eshan.sharma108@gmail.com DELTA tables/2e20e446-5149-443d-a5e6-2c8f0e948b27 datawarehouse gold fact_sales MANAGED YES PRESERVE eshan.sharma108@gmail.com null 2026-02-08T08:37:45.792Z eshan.sharma108@gmail.com 2026-02-08T08:37:46.494Z eshan.sharma108@gmail.com DELTA tables/53cf3f26-d7e2-462b-8435-c699b9f51e9e datawarehouse gold dim_customers MANAGED YES PRESERVE eshan.sharma108@gmail.com null 2026-02-08T08:37:04.357Z eshan.sharma108@gmail.com 2026-02-08T08:37:05.225Z eshan.sharma108@gmail.com DELTA tables/d8b24fa7-d2d5-4edb-8fee-bfd0eb69318b datawarehouse gold report_products MANAGED YES PRESERVE eshan.sharma108@gmail.com null 2026-02-08T16:16:03.190Z eshan.sharma108@gmail.com 2026-02-08T16:16:03.912Z eshan.sharma108@gmail.com DELTA tables/da988393-71f9-4378-8fc2-3a73a5bb5a80 datawarehouse gold dim_products MANAGED YES PRESERVE eshan.sharma108@gmail.com null 2026-02-08T08:37:24.998Z eshan.sharma108@gmail.com 2026-02-08T08:37:25.873Z eshan.sharma108@gmail.com DELTA tables/fa0539dd-bd19-4a88-852a-e93ba63a3e34

In [0]:
spark.sql("""
SELECT * 
FROM information_schema.columns
WHERE table_schema = 'gold'
""").display()

table_catalog table_schema table_name column_name ordinal_position column_default is_nullable full_data_type data_type character_maximum_length character_octet_length numeric_precision numeric_precision_radix numeric_scale datetime_precision interval_type interval_precision maximum_cardinality is_identity identity_generation identity_start identity_increment identity_maximum identity_minimum identity_cycle is_generated generation_expression is_system_time_period_start is_system_time_period_end system_time_period_timestamp_generation is_updatable partition_index comment datawarehouse gold dim_customers customer_key 0 null YES int INT null null null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers customer_id 1 null YES int INT null null null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers customer_number 2 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers first_name 3 null YES string STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers last_name 4 null YES string STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers gender 5 null YES string STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers birth_date 6 null YES date DATE null null null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers country 7 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers marital_status 8 null YES string STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_customers create_date 9 null YES date DATE null null null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products product_key 0 null YES int INT null null null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products product_id 1 null YES int INT null null null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products product_number 2 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products product_name 3 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products category_id 4 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products category 5 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products sub_category 6 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products maintenance 7 null YES varchar(50) STRING 0 0 null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products product_cost 8 null YES int INT null null null null null null null null null NO null null null null null null NO null NO NO null YES null null datawarehouse gold dim_products product_line 9 null YES varchar(50)

## Step 3. Dimension exploration
Understand categorical distributions

In [0]:
cust_df.select("country").distinct().display()
prod_df.select("category").distinct().display()
prod_df.select("sub_category").distinct().display()
prod_df.select('product_name').distinct().display()
prod_df.select("category",'sub_category',"product_name").distinct().orderBy("category","sub_category","product_name").display()

country Australia United States Canada Germany United Kingdom France n/a

category Components Bikes Clothing Accessories null

sub_category Road Frames Mountain Bikes Road Bikes Mountain Frames Socks Forks Wheels Gloves Headsets Locks Lights Panniers Pumps Bib-Shorts Shorts Tights Bottom Brackets Bottles and Cages Touring Bikes Caps Chains Cleaners Cranksets Brakes Derailleurs Fenders Touring Frames Handlebars Helmets Hydration Packs Jerseys Tires and Tubes Bike Racks Saddles Bike Stands Vests null

product_name HL Road Frame - Black- 58 HL Road Frame - Red- 58 Mountain-100 Black- 38 Mountain-100 Black- 42 Mountain-100 Black- 44 Mountain-100 Black- 48 Mountain-100 Silver- 38 Mountain-100 Silver- 42 Mountain-100 Silver- 44 Mountain-100 Silver- 48 Road-450 Red- 44 Road-450 Red- 48 Road-450 Red- 52 Road-450 Red- 58 Road-450 Red- 60 Road-150 Red- 44 Road-150 Red- 48 Road-150 Red- 52 Road-150 Red- 56 Road-150 Red- 62 HL Mountain Frame - Black- 44 HL Mountain Frame - Black- 48 HL Mountain Frame - Silver- 44 HL Mountain Frame - Silver- 48 ML Road Frame - Red- 44 ML Road Frame - Red- 48 ML Road Frame - Red- 52 ML Road Frame - Red- 58 ML Road Frame - Red- 60 Mountain Bike Socks- L Mountain Bike Socks- M Mountain-300 Black- 38 Mountain-300 Black- 40 Mountain-300 Black- 44 Mountain-300 Black- 48 Road-650 Black- 44 Road-650 Black- 48 Road-650 Black- 52 Road-650 Black- 58 Road-650 Black- 60 Road-650 Black- 62 Road-650 Red- 44 Road-650 Red- 48 Road-650 Red- 52 Road-650 Red- 58 Road-650 Red- 60 Road-650 Red- 62 Road-250 Red- 44 Road-250 Red- 48 Road-250 Red- 52 LL Fork ML Fork HL Fork ML Mountain Frame - Black- 38 ML Mountain Frame - Black- 40 ML Mountain Frame - Black- 44 ML Mountain Frame - Black- 48 LL Road Frame - Red- 44 LL Road Frame - Red- 48 LL Road Frame - Red- 52 LL Road Frame - Red- 58 LL Road Frame - Red- 60 LL Road Frame - Red- 62 LL Mountain Front Wheel ML Mountain Front Wheel HL Mountain Front Wheel LL Road Front Wheel ML Road Front Wheel HL Road Front Wheel Touring Front Wheel Full-Finger Gloves- L Full-Finger Gloves- M Full-Finger Gloves- S LL Headset ML Headset HL Headset Cable Lock Headlights - Dual-Beam Headlights - Weatherproof Taillights - Battery-Powered Touring-Panniers- Large Minipump Mountain Pump LL Mountain Rear Wheel ML Mountain Rear Wheel HL Mountain Rear Wheel LL Road Rear Wheel ML Road Rear Wheel HL Road Rear Wheel Touring Rear Wheel Men's Bib-Shorts- L Men's Bib-Shorts- M Men's Bib-Shorts- S Men's Sports Shorts- L Men's Sports Shorts- M Men's Sports Shorts- S Men's Sports Shorts- XL Women's Tights- L Women's Tights- M Women's Tights- S LL Bottom Bracket ML Bottom Bracket HL Bottom Bracket Mountain Bottle Cage Road Bottle Cage Mountain-500 Black- 40 Mountain-500 Black- 42 Mountain-500 Black- 44 Mountain-500 Black- 48 Mountain-500 Black- 52 Mountain-500 Silver- 40 Mountain-500 Silver- 42 Mountain-500 Silver- 44 Mountain-500 Silver- 48 Mountain-500 Silver- 52 Mountain-400-W Silver- 38 Mountain-400-W Silver- 40 Mountain-400-W Silver- 42 Mountain-400-W Silver- 46 Mountain-200 Black- 38 Mountain-200 Black- 42 Mountain-200 Black- 46 Mountain-200 Silver- 38 Mountain-200 Silver- 42 Mountain-200 Silver- 46 Road-750 Black- 44 Road-750 Black- 48 Road-750 Black- 52 Road-750 Black- 58 Road-550-W Yellow- 38 Road-550-W Yellow- 40 Road-550-W Yellow- 42 Road-550-W Yellow- 44 Road-550-W Yellow- 48 Road-350-W Yellow- 40 Road-350-W Yellow- 42 Road-350-W Yellow- 44 Road-350-W Yellow- 48 Road-250 Black- 44 Road-250 Black- 48 Road-250 Black- 52 Road-250 Black- 58 Road-250 Red- 58 Touring-3000 Blue- 44 Touring-3000 Blue- 50 Touring-3000 Blue- 54 Touring-3000 Blue- 58 Touring-3000 Blue- 62 Touring-3000 Yellow- 44 Touring-3000 Yellow- 50 Touring-3000 Yellow- 54 Touring-3000 Yellow- 58 Touring-3000 Yellow- 62 Touring-2000 Blue- 46 Touring-2000 Blue- 50 Touring-2000 Blue- 54 Touring-2000 Blue- 60 Touring-1000 Blue- 46 Touring-1000 Blue- 50 Touring-1000 Blue- 54 Touring-1000 Blue- 60 Touring-1000 Yellow- 46 Touring-1000 Yellow- 50 Touring-1000 Yellow- 54 Touring-1000 Yellow- 60 AWC Logo Cap Chain Bike Wash - Dissolver LL Crankset ML Crankset HL Crankset Front Brakes Front Derailleur Fender Set - Mountain LL Mountain Frame - Black- 40 LL Mountain Frame - Black- 42 LL Mountain Frame - Black- 44 LL Mountain Frame - Black- 48 LL Mountain Frame - Black- 52 LL Mountain Frame - Silver- 40 LL Mountain Frame - Silver- 42 LL Mountain Frame - Silver- 44 LL Mountain Frame - Silver- 48 LL Mountain Frame - Silver- 52 ML Mountain Frame-W - Silver- 

category sub_category product_name null null HL Mountain Pedal null null HL Road Pedal null null LL Mountain Pedal null null LL Road Pedal null null ML Mountain Pedal null null ML Road Pedal null null Touring Pedal Accessories Bike Racks Hitch Rack - 4-Bike Accessories Bike Stands All-Purpose Bike Stand Accessories Bottles and Cages Mountain Bottle Cage Accessories Bottles and Cages Road Bottle Cage Accessories Bottles and Cages Water Bottle - 30 oz. Accessories Cleaners Bike Wash - Dissolver Accessories Fenders Fender Set - Mountain Accessories Helmets Sport-100 Helmet- Black Accessories Helmets Sport-100 Helmet- Blue Accessories Helmets Sport-100 Helmet- Red Accessories Hydration Packs Hydration Pack - 70 oz. Accessories Lights Headlights - Dual-Beam Accessories Lights Headlights - Weatherproof Accessories Lights Taillights - Battery-Powered Accessories Locks Cable Lock Accessories Panniers Touring-Panniers- Large Accessories Pumps Minipump Accessories Pumps Mountain Pump Accessories Tires and Tubes HL Mountain Tire Accessories Tires and Tubes HL Road Tire Accessories Tires and Tubes LL Mountain Tire Accessories Tires and Tubes LL Road Tire Accessories Tires and Tubes ML Mountain Tire Accessories Tires and Tubes ML Road Tire Accessories Tires and Tubes Mountain Tire Tube Accessories Tires and Tubes Patch Kit/8 Patches Accessories Tires and Tubes Road Tire Tube Accessories Tires and Tubes Touring Tire Accessories Tires and Tubes Touring Tire Tube Bikes Mountain Bikes Mountain-100 Black- 38 Bikes Mountain Bikes Mountain-100 Black- 42 Bikes Mountain Bikes Mountain-100 Black- 44 Bikes Mountain Bikes Mountain-100 Black- 48 Bikes Mountain Bikes Mountain-100 Silver- 38 Bikes Mountain Bikes Mountain-100 Silver- 42 Bikes Mountain Bikes Mountain-100 Silver- 44 Bikes Mountain Bikes Mountain-100 Silver- 48 Bikes Mountain Bikes Mountain-200 Black- 38 Bikes Mountain Bikes Mountain-200 Black- 42 Bikes Mountain Bikes Mountain-200 Black- 46 Bikes Mountain Bikes Mountain-200 Silver- 38 Bikes Mountain Bikes Mountain-200 Silver- 42 Bikes Mountain Bikes Mountain-200 Silver- 46 Bikes Mountain Bikes Mountain-300 Black- 38 Bikes Mountain Bikes Mountain-300 Black- 40 Bikes Mountain Bikes Mountain-300 Black- 44 Bikes Mountain Bikes Mountain-300 Black- 48 Bikes Mountain Bikes Mountain-400-W Silver- 38 Bikes Mountain Bikes Mountain-400-W Silver- 40 Bikes Mountain Bikes Mountain-400-W Silver- 42 Bikes Mountain Bikes Mountain-400-W Silver- 46 Bikes Mountain Bikes Mountain-500 Black- 40 Bikes Mountain Bikes Mountain-500 Black- 42 Bikes Mountain Bikes Mountain-500 Black- 44 Bikes Mountain Bikes Mountain-500 Black- 48 Bikes Mountain Bikes Mountain-500 Black- 52 Bikes Mountain Bikes Mountain-500 Silver- 40 Bikes Mountain Bikes Mountain-500 Silver- 42 Bikes Mountain Bikes Mountain-500 Silver- 44 Bikes Mountain Bikes Mountain-500 Silver- 48 Bikes Mountain Bikes Mountain-500 Silver- 52 Bikes Road Bikes Road-150 Red- 44 Bikes Road Bikes Road-150 Red- 48 Bikes Road Bikes Road-150 Red- 52 Bikes Road Bikes Road-150 Red- 56 Bikes Road Bikes Road-150 Red- 62 Bikes Road Bikes Road-250 Black- 44 Bikes Road Bikes Road-250 Black- 48 Bikes Road Bikes Road-250 Black- 52 Bikes Road Bikes Road-250 Black- 58 Bikes Road Bikes Road-250 Red- 44 Bikes Road Bikes Road-250 Red- 48 Bikes Road Bikes Road-250 Red- 52 Bikes Road Bikes Road-250 Red- 58 Bikes Road Bikes Road-350-W Yellow- 40 Bikes Road Bikes Road-350-W Yellow- 42 Bikes Road Bikes Road-350-W Yellow- 44 Bikes Road Bikes Road-350-W Yellow- 48 Bikes Road Bikes Road-450 Red- 44 Bikes Road Bikes Road-450 Red- 48 Bikes Road Bikes Road-450 Red- 52 Bikes Road Bikes Road-450 Red- 58 Bikes Road Bikes Road-450 Red- 60 Bikes Road Bikes Road-550-W Yellow- 38 Bikes Road Bikes Road-550-W Yellow- 40 Bikes Road Bikes Road-550-W Yellow- 42 Bikes Road Bikes Road-550-W Yellow- 44 Bikes Road Bikes Road-550-W Yellow- 48 Bikes Road Bikes Road-650 Black- 44 Bikes Road Bikes Road-650 Black- 48 Bikes Road Bikes Road-650 Black- 52 Bikes Road Bikes 

## Step 4. Date exploration
Check data coverage

In [0]:
fact_df.select("order_date").display()

order_date 2010-12-29 2010-12-29 2010-12-29 2010-12-29 2010-12-29 2010-12-30 2010-12-30 2010-12-30 2010-12-30 2010-12-31 2010-12-31 2010-12-31 2010-12-31 2010-12-31 2011-01-01 2011-01-01 2011-01-02 2011-01-02 2011-01-02 2011-01-02 2011-01-02 2011-01-03 2011-01-03 2011-01-03 2011-01-03 2011-01-04 2011-01-04 2011-01-04 2011-01-05 2011-01-05 2011-01-05 2011-01-06 2011-01-06 2011-01-06 2011-01-06 2011-01-06 2011-01-06 2011-01-07 2011-01-07 2011-01-07 2011-01-08 2011-01-08 2011-01-08 2011-01-08 2011-01-09 2011-01-09 2011-01-09 2011-01-09 2011-01-10 2011-01-10 2011-01-11 2011-01-11 2011-01-11 2011-01-11 2011-01-11 2011-01-11 2011-01-11 2011-01-12 2011-01-12 2011-01-12 2011-01-12 2011-01-13 2011-01-13 2011-01-13 2011-01-13 2011-01-14 2011-01-14 2011-01-14 2011-01-14 2011-01-15 2011-01-15 2011-01-16 2011-01-16 2011-01-16 2011-01-16 2011-01-16 2011-01-16 2011-01-16 2011-01-16 2011-01-17 2011-01-17 2011-01-17 2011-01-17 2011-01-18 2011-01-18 2011-01-18 2011-01-18 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-19 2011-01-20 2011-01-20 2011-01-20 2011-01-20 2011-01-20 2011-01-21 2011-01-21 2011-01-21 2011-01-22 2011-01-22 2011-01-22 2011-01-22 2011-01-23 2011-01-23 2011-01-23 2011-01-23 2011-01-23 2011-01-24 2011-01-24 2011-01-24 2011-01-24 2011-01-24 2011-01-24 2011-01-24 2011-01-24 2011-01-25 2011-01-25 2011-01-25 2011-01-25 2011-01-25 2011-01-25 2011-01-25 2011-01-25 2011-01-26 2011-01-26 2011-01-26 2011-01-26 2011-01-26 2011-01-27 2011-01-27 2011-01-27 2011-01-27 2011-01-27 2011-01-28 2011-01-28 2011-01-28 2011-01-28 2011-01-28 2011-01-29 2011-01-29 2011-01-29 2011-01-29 2011-01-29 2011-01-30 2011-01-30 2011-01-30 2011-01-31 2011-01-31 2011-01-31 2011-01-31 2011-02-01 2011-02-01 2011-02-01 2011-02-01 2011-02-01 2011-02-02 2011-02-02 2011-02-02 2011-02-02 2011-02-02 2011-02-02 2011-02-03 2011-02-03 2011-02-03 2011-02-03 2011-02-03 2011-02-03 2011-02-03 2011-02-03 2011-02-04 2011-02-04 2011-02-04 2011-02-04 2011-02-05 2011-02-05 2011-02-05 2011-02-05 2011-02-06 2011-02-06 2011-02-06 2011-02-06 2011-02-07 2011-02-07 2011-02-07 2011-02-07 2011-02-07 2011-02-07 2011-02-08 2011-02-08 2011-02-08 2011-02-08 2011-02-08 2011-02-09 2011-02-09 2011-02-09 2011-02-09 2011-02-09 2011-02-09 2011-02-10 2011-02-10 2011-02-10 2011-02-10 2011-02-10 2011-02-11 2011-02-11 2011-02-11 2011-02-11 2011-02-12 2011-02-12 2011-02-12 2011-02-12 2011-02-12 2011-02-12 2011-02-14 2011-02-15 2011-02-15 2011-02-15 2011-02-15 2011-02-15 2011-02-15 2011-02-16 2011-02-16 2011-02-16 2011-02-16 2011-02-16 2011-02-16 2011-02-16 2011-02-16 2011-02-17 2011-02-17 2011-02-17 2011-02-17 2011-02-17 2011-02-17 2011-02-18 2011-02-18 2011-02-18 2011-02-18 2011-02-18 2011-02-18 2011-02-18 2011-02-18 2011-02-19 2011-02-19 2011-02-19 2011-02-19 2011-02-19 2011-02-20 2011-02-20 2011-02-20 2011-02-21 2011-02-21 2011-02-21 2011-02-21 2011-02-21 2011-02-21 2011-02-21 2011-02-21 2011-02-21 2011-02-22 2011-02-22 2011-02-22 2011-02-23 2011-02-23 2011-02-23 2011-02-23 2011-02-23 2011-02-23 2011-02-23 2011-02-24 2011-02-24 2011-02-25 2011-02-25 2011-02-26 2011-02-26 2011-02-26 2011-02-26 2011-02-26 2011-02-26 2011-02-26 2011-02-26 2011-02-27 2011-02-27 2011-02-27 2011-02-27 2011-02-27 2011-02-27 2011-02-27 2011-02-28 2011-02-28 2011-02-28 2011-02-28 2011-02-28 2011-02-28 2011-03-01 2011-03-01 2011-03-01 2011-03-01 2011-03-02 2011-03-02 2011-03-02 2011-03-02 2011-03-02 2011-03-02 2011-03-02 2011-03-02 2011-03-02 2011-03-02 2011-03-03 2011-03-03 2011-03-03 2011-03-03 2011-03-04 2011-03-04 2011-03-04 2011-03-04 2011-03-04 2011-03-04 2011-03-05 2011-03-05 2011-03-05 2011-03-06 2011-03-06 2011-03-06 2011-03-06 2011-03-06 2011-03-06 2011-03-06 2011-03-07 2011-03-07 2011-03-07 2011-03-07 2011-03-07 2011-03-08 2011-03-08 2011-03-08 2011-03-09 2011-03-09 2011-03-09 2011-03-09 2011-03-09 2011-03-09 2011-03-09 2011-03-10 2011-03-10 2011-03-10 2011-03-12 2011-03-12 2011-03-13 2011-03-13 2011-03-13 2011-03-13 2011-03-14 2011-03-14 2011-03

Check first and last order date

In [0]:
fact_df.agg(
    F.min("order_date").alias("first_order"),
    F.max("order_date").alias("last_order")
).display()

first_order last_order 2010-12-29 2014-01-28

How many years of sales are available?

In [0]:

fact_df.agg(
    F.min("order_date").alias("first_order"),
    F.max("order_date").alias("last_order"),
    F.floor(
        F.months_between(F.max("order_date"), F.min("order_date")) / 12
    ).alias("years_of_sales"),
    F.floor(
        F.months_between(F.max("order_date"), F.min("order_date"))
    ).alias("months_of_sales")
).display()

first_order last_order years_of_sales months_of_sales 2010-12-29 2014-01-28 3 36

Finding the youngest and oldest customer birth dates

In [0]:
cust_df.agg(
    F.min("birth_date").alias("oldest_birthdate"),
    F.max("birth_date").alias("youngest_birthdate")
).display()

oldest_birthdate youngest_birthdate 1926-03-15 1986-06-25

Finding the ages of youngest and oldest customer

In [0]:
cust_df.agg(
    F.floor(F.months_between(F.current_date(), F.min("birth_date")) / 12).alias("oldest_age"),
    F.floor(F.months_between(F.current_date(), F.max("birth_date")) / 12).alias("youngest_age")
).display()


oldest_age youngest_age 99 39

## Step 5. Core metrics (Measures Exploration)
High-level KPIs

In [0]:

# Fact metrics
fact_metrics = fact_df.agg(
    F.sum("sales_amount").alias("total_sales"),
    F.sum("quantity").alias("total_quantity"),
    F.avg("price").alias("avg_price"),
    F.count("order_number").alias("total_orders"),                 # includes duplicates
    F.countDistinct("order_number").alias("total_orders_unique"),  # unique orders
    F.countDistinct("customer_key").alias("active_customers")      # customers who ordered
)

# Dimension metrics
product_metrics = prod_df.agg(
    F.count("product_key").alias("total_products")
)

customer_metrics = cust_df.agg(
    F.count("customer_key").alias("total_customers"),
    F.countDistinct("customer_key").alias("active_customers")
)

# Combine everything into one row
metrics_df = (
    fact_metrics
    .crossJoin(product_metrics)
    .crossJoin(customer_metrics)
)

metrics_df.display()

total_sales total_quantity avg_price total_orders total_orders_unique active_customers total_products total_customers active_customers 2.935625E7 60423 486.0377827080367 60398 27659 18484 295 18484 18484

## Step 6. Magnitude Analysis

In [0]:

# Customers by country

customers_by_country_df = (
    cust_df
    .groupBy("country")
    .agg(F.count("customer_key").alias("total_customers"))
    .orderBy(F.desc("total_customers"))
)
customers_by_country_df.display()

country total_customers United States 7482 Australia 3591 United Kingdom 1913 France 1810 Germany 1780 Canada 1571 n/a 337

In [0]:
# Customers by gender
customers_by_gender_df = (
    cust_df
    .groupBy("gender")
    .agg(F.count("customer_key").alias("total_customers"))
    .orderBy(F.desc("total_customers"))
)
customers_by_gender_df.display()

gender total_customers Male 9341 Female 9128 n/a 15

In [0]:
# Products by category
products_by_category_df = (
    prod_df
    .groupBy("category")
    .agg(F.count("product_key").alias("total_products"))
    .orderBy(F.desc("total_products"))
)
products_by_category_df.display()

category total_products Components 127 Bikes 97 Clothing 35 Accessories 29 null 7

In [0]:
# Average cost per category
avg_cost_by_category_df = (
    prod_df
    .groupBy("category")
    .agg(F.avg("product_cost").alias("avg_costs"))
    .orderBy(F.desc("avg_costs"))
)
avg_cost_by_category_df.display()

category avg_costs Bikes 949.4432989690722 Components 264.7165354330709 null 28.571428571428573 Clothing 24.8 Accessories 13.172413793103448

## Step 7. Revenue

In [0]:
#Revenue by Category
category_sales = (
    fact_df.join(prod_df, "product_key", "left")
    .groupBy("category")
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy(F.desc("total_sales"))
)

category_sales.display()

category total_sales Bikes 2.8316272E7 Accessories 700262.0 Clothing 339716.0

In [0]:
# Revenue by customer
revenue_by_customer_df = (
    fact_df
    .join(cust_df, "customer_key", "left")
    .groupBy("customer_key")
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy(F.desc("total_sales"))
)
revenue_by_customer_df.display()

customer_key total_sales 1302 13294.0 1133 13294.0 1309 13268.0 1132 13265.0 1301 13242.0 1322 13215.0 1125 13195.0 1308 13172.0 1297 13164.0 434 12914.0 440 12488.0 242 11468.0 418 11248.0 421 11200.0 243 11067.0 1656 10899.0 2264 10871.0 1324 10836.0 1334 10829.0 1651 10813.0 1632 10799.0 1633 10793.0 1333 10789.0 2406 10778.0 246 10580.0 247 10575.0 238 10566.0 426 10528.0 430 10468.0 429 9954.0 428 9918.0 432 9913.0 424 9905.0 250 9890.0 413 9880.0 3187 9796.0 422 9780.0 2593 9695.0 2606 9614.0 3186 9524.0 2576 9458.0 3193 9452.0 2578 9451.0 3201 9422.0 2596 9391.0 433 9330.0 2258 8941.0 2259 8886.0 1129 8681.0 1126 8595.0 1130 8557.0 2601 8460.0 3428 8451.0 4107 8421.0 3776 8404.0 3430 8394.0 4693 8392.0 4098 8377.0 2603 8376.0 2584 8375.0 2582 8375.0 2586 8368.0 3941 8367.0 3940 8367.0 2585 8361.0 3208 8361.0 2592 8355.0 3831 8346.0 4692 8341.0 3426 8332.0 2577 8330.0 3182 8326.0 4696 8324.0 3184 8321.0 3429 8321.0 768 8319.0 3427 8319.0 3190 8317.0 3196 8316.0 3199 8308.0 2591 8306.0 4081 8305.0 3192 8301.0 4119 8301.0 4355 8297.0 113 8295.0 767 8280.0 1339 8265.0 102 8262.0 901 8257.0 1004 8256.0 452 8250.0 996 8249.0 1 8249.0 59 8248.0 902 8248.0 110 8245.0 987 8245.0 121 8242.0 447 8237.0 444 8235.0 763 8228.0 457 8224.0 895 8223.0 55 8223.0 344 8222.0 100 8216.0 752 8215.0 905 8214.0 978 8213.0 1040 8212.0 8 8211.0 458 8211.0 57 8207.0 919 8205.0 81 8204.0 898 8203.0 1011 8203.0 5 8196.0 1010 8195.0 148 8195.0 73 8194.0 342 8192.0 900 8189.0 118 8185.0 1001 8183.0 453 8183.0 104 8182.0 94 8180.0 899 8179.0 917 8179.0 454 8177.0 451 8173.0 970 8173.0 965 8173.0 105 8173.0 920 8172.0 101 8172.0 108 8171.0 78 8169.0 995 8169.0 953 8169.0 56 8168.0 915 8166.0 71 8165.0 473 8165.0 991 8164.0 755 8163.0 334 8163.0 338 8162.0 395 8162.0 382 8161.0 77 8159.0 96 8158.0 492 8158.0 466 8158.0 906 8156.0 921 8156.0 335 8154.0 968 8153.0 61 8153.0 907 8151.0 762 8149.0 896 8149.0 751 8148.0 1003 8145.0 916 8143.0 483 8143.0 766 8143.0 456 8142.0 460 8141.0 990 8140.0 769 8139.0 4 8139.0 1338 8137.0 461 8137.0 112 8137.0 445 8136.0 908 8135.0 12 8133.0 449 8132.0 53 8131.0 994 8131.0 450 8130.0 62 8129.0 765 8129.0 125 8129.0 465 8128.0 992 8128.0 490 8127.0 109 8124.0 993 8123.0 894 8123.0 6 8121.0 918 8121.0 345 8119.0 893 8119.0 7 8119.0 897 8118.0 463 8116.0 1005 8114.0 399 8114.0 3 8114.0 911 8113.0 1002 8113.0 93 8110.0 904 8108.0 9 8106.0 910 8105.0 70 8104.0 98 8099.0 446 8098.0 106 8096.0 913 8095.0 111 8093.0 1303 8091.0 10 8091.0 489 8090.0 455 8089.0 462 8089.0 11 8088.0 58 8088.0 977 8087.0 152 8087.0 969 8079.0 909 8079.0 107 8079.0 354 8078.0 757 8078.0 448 8078.0 989 8078.0 76 8068.0 964 8068.0 352 8068.0 1292 8067.0 97 8063.0 760 8054.0 1299 8052.0 1298 8022.0 1315 7997.0 1131 7987.0 1331 7932.0 2260 7853.0 241 7586.0 239 7543.0 240 7511.0 2257 7494.0 2256 7393.0 1658 7384.0 5590 7343.0 2407 7300.0 2580 7294.0 6222 7292.0 2581 7285.0 6115 7275.0 4094 7265.0 2265 7265.0 2266 7259.0 4096 7255.0 6185 7253.0 4624 7247.0 5264 7243.0 5824 7242.0 2261 7239.0 5197 7237.0 6199 7233.0 4358 7232.0 5595 7231.0 4086 7229.0 8032 7226.0 5208 7226.0 4677 7224.0 4679 7223.0 5822 7221.0 2793 7216.0 2795 7212.0 4117 7212.0 6215 7211.0 3792 7210.0 5832 7206.0 4676 7206.0 5828 7205.0 5207 7203.0 5566 7203.0 7167 7200.0 4678 7200.0 2262 7200.0 2607 7195.0 5586 7192.0 415 7191.0 414 7190.0 7174 7189.0 4686 7188.0 6782 7187.0 4933 7186.0 5830 7185.0 6210 7182.0 5829 7182.0 5823 7176.0 245 7175.0 6184 7175.0 2694 7171.0 5262 7170.0 4626 7169.0 244 7164.0 5205 7162.0 2691 7162.0 5568 7159.0 2766 7152.0 2778 7147.0 5831 7138.0 2785 7138.0 248 7131.0 5599 7131.0 251 7115.0 4095 7109.0 1038 7107.0 3204 7082.0 423 7075.0 4083 7069.0 549 7068.0 5588 7064.0 997 7059.0 486 7049.0 7178 7044.0 1000 7043.0 3977 7041.0 998 7030.0 4627 7029.0 1008 7024.0 550 7024.0 2013 7017.0 6826 7016.0 3774 7016.0 497 7014.0 3791 7005.0 5604 7001.0 5299 7001.0 4638 7000.0 4085 7000.0 3425 6999.0 6200 6998.0 5576 6995.0 5589 6995.0 6812 6990.0 4625 6990.0 389 6987.

In [0]:
# Sales distribution by country
sales_by_country_df = (
    fact_df
    .join(cust_df, "customer_key", "left")
    .groupBy("country")
    .agg(F.sum("sales_amount").alias("total_sold_items"))
    .orderBy(F.desc("total_sold_items"))
)
sales_by_country_df.display()

country total_sold_items United States 9162327.0 Australia 9060172.0 United Kingdom 3391376.0 Germany 2894066.0 France 2643751.0 Canada 1977738.0 n/a 226820.0

## Step 8. Ranking Analysis

In [0]:
fact_products_df = fact_df.join(prod_df, "product_key", "left")
fact_customers_df = fact_df.join(cust_df, "customer_key", "left")

In [0]:
#Top 5 products by revenue
top_products= (
    fact_products_df
    .groupBy("product_key")
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy(F.desc("total_sales"))
    .limit(5)
)


top_products.display()

product_key total_sales 122 1373454.0 121 1363128.0 123 1339394.0 125 1301029.0 120 1294854.0

In [0]:
#Bottom 5 products by revenue
bottom_products_df = (
    fact_products_df
    .groupBy("product_key")
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy("total_sales")
    .limit(5)
)
bottom_products_df.display()

product_key total_sales 279 2430.0 280 2682.0 259 6382.0 168 7272.0 291 7440.0

In [0]:
#Top 5 subcategories by revenue
top_subcategories_df = (
    fact_products_df
    .groupBy("sub_category")
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy(F.desc("total_sales"))
    .limit(5)
)
top_subcategories_df.display()

sub_category total_sales Road Bikes 1.4519438E7 Mountain Bikes 9952254.0 Touring Bikes 3844580.0 Tires and Tubes 244634.0 Helmets 225435.0

In [0]:
#Top 10 customers by revenue
top_customers_df = (
    fact_customers_df
    .groupBy("customer_key")
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy(F.desc("total_sales"))
    .limit(10)
)
top_customers_df.display()

customer_key total_sales 1133 13294.0 1302 13294.0 1309 13268.0 1132 13265.0 1301 13242.0 1322 13215.0 1125 13195.0 1308 13172.0 1297 13164.0 434 12914.0

In [0]:
#Bottom 3 customers with fewest orders
bottom_customers_orders_df = (
    fact_customers_df
    .groupBy("customer_key")
    .agg(F.countDistinct("order_number").alias("total_orders"))
    .orderBy("total_orders")
    .limit(3)
)
bottom_customers_orders_df.display()

customer_key total_orders 17390 1 16602 1 16613 1

## Step 9. Change Over Time Analysis

In [0]:
sales_df = (
    fact_df
    .filter(F.col("order_date").isNotNull())
)


In [0]:
#Yearly total sales
yearly_sales_df = (
    sales_df
    .groupBy(F.year("order_date").alias("order_year"))
    .agg(
        F.sum("sales_amount").alias("total_sales")
    )
    .orderBy("order_year")
)
yearly_sales_df.display()

order_year total_sales 2010 43419.0 2011 7075088.0 2012 5842231.0 2013 1.6344878E7 2014 45642.0

In [0]:
#Yearly total sales + customers
yearly_sales_customers_df = (
    sales_df
    .groupBy(F.year("order_date").alias("order_year"))
    .agg(
        F.sum("sales_amount").alias("total_sales"),
        F.countDistinct("customer_key").alias("total_customers")
    )
    .orderBy("order_year")
)
yearly_sales_customers_df.display()

order_year total_sales total_customers 2010 43419.0 14 2011 7075088.0 2216 2012 5842231.0 3255 2013 1.6344878E7 17427 2014 45642.0 834

In [0]:
#Yearly sales + customers + quantity
yearly_full_df = (
    sales_df
    .groupBy(F.year("order_date").alias("order_year"))
    .agg(
        F.sum("sales_amount").alias("total_sales"),
        F.countDistinct("customer_key").alias("total_customers"),
        F.sum("quantity").alias("total_quantity")
    )
    .orderBy("order_year")
)
yearly_full_df.display()

order_year total_sales total_customers total_quantity 2010 43419.0 14 14 2011 7075088.0 2216 2216 2012 5842231.0 3255 3397 2013 1.6344878E7 17427 52807 2014 45642.0 834 1970

In [0]:
#Monthly seasonality
monthly_trends_df = (
    sales_df
    .groupBy(F.month("order_date").alias("order_month"))
    .agg(
        F.sum("sales_amount").alias("total_sales"),
        F.countDistinct("customer_key").alias("total_customers"),
        F.sum("quantity").alias("total_quantity")
    )
    .orderBy("order_month")
)
monthly_trends_df.display()

order_month total_sales total_customers total_quantity 1 1868558.0 1818 4043 2 1744517.0 1765 3858 3 1908375.0 1982 4449 4 1948226.0 1916 4355 5 2204969.0 2074 4781 6 2935883.0 2430 5573 7 2412838.0 2154 5107 8 2684313.0 2312 5335 9 2536520.0 2210 5070 10 2916550.0 2533 5838 11 2979113.0 2500 5756 12 3211396.0 2656 6239

In [0]:
# Year + month breakdown
year_month_df = (
    sales_df
    .groupBy(
        F.year("order_date").alias("order_year"),
        F.month("order_date").alias("order_month")
    )
    .agg(
        F.sum("sales_amount").alias("total_sales"),
        F.countDistinct("customer_key").alias("total_customers"),
        F.sum("quantity").alias("total_quantity")
    )
    .orderBy("order_year", "order_month")
)
year_month_df.display()

order_year order_month total_sales total_customers total_quantity 2010 12 43419.0 14 14 2011 1 469795.0 144 144 2011 2 466307.0 144 144 2011 3 485165.0 150 150 2011 4 502042.0 157 157 2011 5 561647.0 174 174 2011 6 737793.0 230 230 2011 7 596710.0 188 188 2011 8 614516.0 193 193 2011 9 603047.0 185 185 2011 10 708164.0 221 221 2011 11 660507.0 208 208 2011 12 669395.0 222 222 2012 1 495363.0 252 252 2012 2 506992.0 260 260 2012 3 373478.0 212 212 2012 4 400324.0 219 219 2012 5 358866.0 207 207 2012 6 555142.0 318 318 2012 7 444533.0 246 246 2012 8 523887.0 294 294 2012 9 486149.0 269 269 2012 10 535125.0 313 313 2012 11 537918.0 324 324 2012 12 624454.0 354 483 2013 1 857758.0 627 1677 2013 2 771218.0 1373 3454 2013 3 1049732.0 1631 4087 2013 4 1045860.0 1564 3979 2013 5 1284456.0 1719 4400 2013 6 1642948.0 1948 5025 2013 7 1371595.0 1796 4673 2013 8 1545910.0 1898 4848 2013 9 1447324.0 1832 4616 2013 10 1673261.0 2073 5304 2013 11 1780688.0 2036 5224 2013 12 1874128.0 2133 5520 2014 1 45642.0 834 1970

## Step 10. Cumulative Analysis

In [0]:
#Total sales per month (month number only)
monthly_sales_df = (
    sales_df
    .groupBy(F.month("order_date").alias("monthly"))
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy("monthly")
)
monthly_sales_df.display()

monthly total_sales 1 1868558.0 2 1744517.0 3 1908375.0 4 1948226.0 5 2204969.0 6 2935883.0 7 2412838.0 8 2684313.0 9 2536520.0 10 2916550.0 11 2979113.0 12 3211396.0

In [0]:
# Running total of sales over time (monthly number 1–12)
w = Window.orderBy("monthly").rowsBetween(Window.unboundedPreceding, Window.currentRow)

running_monthly_df = (
    monthly_sales_df
    .withColumn("running_total_sales", F.sum("total_sales").over(w))
)
running_monthly_df.display()

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


monthly total_sales running_total_sales 1 1868558.0 1868558.0 2 1744517.0 3613075.0 3 1908375.0 5521450.0 4 1948226.0 7469676.0 5 2204969.0 9674645.0 6 2935883.0 1.2610528E7 7 2412838.0 1.5023366E7 8 2684313.0 1.7707679E7 9 2536520.0 2.0244199E7 10 2916550.0 2.3160749E7 11 2979113.0 2.6139862E7 12 3211396.0 2.9351258E7

In [0]:
#Running total using real calendar months (DATE_TRUNC('month'))
#(this is usually what you actually want for time series, because Jan 2023 ≠ Jan 2024)
monthly_calendar_df = (
    sales_df
    .groupBy(F.date_trunc("month", "order_date").alias("monthly"))
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy("monthly")
)

w_cal = Window.orderBy("monthly").rowsBetween(Window.unboundedPreceding, Window.currentRow)

running_calendar_df = (
    monthly_calendar_df
    .withColumn("running_total_sales", F.sum("total_sales").over(w_cal))
)
running_calendar_df.display()

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


monthly total_sales running_total_sales 2010-12-01T00:00:00.000Z 43419.0 43419.0 2011-01-01T00:00:00.000Z 469795.0 513214.0 2011-02-01T00:00:00.000Z 466307.0 979521.0 2011-03-01T00:00:00.000Z 485165.0 1464686.0 2011-04-01T00:00:00.000Z 502042.0 1966728.0 2011-05-01T00:00:00.000Z 561647.0 2528375.0 2011-06-01T00:00:00.000Z 737793.0 3266168.0 2011-07-01T00:00:00.000Z 596710.0 3862878.0 2011-08-01T00:00:00.000Z 614516.0 4477394.0 2011-09-01T00:00:00.000Z 603047.0 5080441.0 2011-10-01T00:00:00.000Z 708164.0 5788605.0 2011-11-01T00:00:00.000Z 660507.0 6449112.0 2011-12-01T00:00:00.000Z 669395.0 7118507.0 2012-01-01T00:00:00.000Z 495363.0 7613870.0 2012-02-01T00:00:00.000Z 506992.0 8120862.0 2012-03-01T00:00:00.000Z 373478.0 8494340.0 2012-04-01T00:00:00.000Z 400324.0 8894664.0 2012-05-01T00:00:00.000Z 358866.0 9253530.0 2012-06-01T00:00:00.000Z 555142.0 9808672.0 2012-07-01T00:00:00.000Z 444533.0 1.0253205E7 2012-08-01T00:00:00.000Z 523887.0 1.0777092E7 2012-09-01T00:00:00.000Z 486149.0 1.1263241E7 2012-10-01T00:00:00.000Z 535125.0 1.1798366E7 2012-11-01T00:00:00.000Z 537918.0 1.2336284E7 2012-12-01T00:00:00.000Z 624454.0 1.2960738E7 2013-01-01T00:00:00.000Z 857758.0 1.3818496E7 2013-02-01T00:00:00.000Z 771218.0 1.4589714E7 2013-03-01T00:00:00.000Z 1049732.0 1.5639446E7 2013-04-01T00:00:00.000Z 1045860.0 1.6685306E7 2013-05-01T00:00:00.000Z 1284456.0 1.7969762E7 2013-06-01T00:00:00.000Z 1642948.0 1.961271E7 2013-07-01T00:00:00.000Z 1371595.0 2.0984305E7 2013-08-01T00:00:00.000Z 1545910.0 2.2530215E7 2013-09-01T00:00:00.000Z 1447324.0 2.3977539E7 2013-10-01T00:00:00.000Z 1673261.0 2.56508E7 2013-11-01T00:00:00.000Z 1780688.0 2.7431488E7 2013-12-01T00:00:00.000Z 1874128.0 2.9305616E7 2014-01-01T00:00:00.000Z 45642.0 2.9351258E7

In [0]:
#Running total of yearly sales
yearly_df = (
    sales_df
    .groupBy(F.date_trunc("year", "order_date").alias("yearly"))
    .agg(F.sum("sales_amount").alias("total_sales"))
    .orderBy("yearly")
)

w_year = Window.orderBy("yearly").rowsBetween(Window.unboundedPreceding, Window.currentRow)

running_yearly_df = (
    yearly_df
    .withColumn("running_total_sales", F.sum("total_sales").over(w_year))
)
running_yearly_df.display()

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


yearly total_sales running_total_sales 2010-01-01T00:00:00.000Z 43419.0 43419.0 2011-01-01T00:00:00.000Z 7075088.0 7118507.0 2012-01-01T00:00:00.000Z 5842231.0 1.2960738E7 2013-01-01T00:00:00.000Z 1.6344878E7 2.9305616E7 2014-01-01T00:00:00.000Z 45642.0 2.9351258E7

In [0]:
#Moving average of yearly sales
yearly_avg_df = (
    sales_df
    .groupBy(F.date_trunc("year", "order_date").alias("yearly"))
    .agg(
        F.sum("sales_amount").alias("total_sales"),
        F.avg("price").alias("avg_price")
    )
    .orderBy("yearly")
)

w_year = Window.orderBy("yearly").rowsBetween(Window.unboundedPreceding, Window.currentRow)

yearly_moving_df = (
    yearly_avg_df
    .withColumn("running_total_sales", F.sum("total_sales").over(w_year))
    .withColumn("moving_average", F.avg("avg_price").over(w_year))
)

yearly_moving_df.display()

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


yearly total_sales avg_price running_total_sales moving_average 2010-01-01T00:00:00.000Z 43419.0 3101.3571428571427 43419.0 3101.3571428571427 2011-01-01T00:00:00.000Z 7075088.0 3192.7292418772563 7118507.0 3147.0431923671995 2012-01-01T00:00:00.000Z 5842231.0 1719.8207241683838 1.2960738E7 2671.302369634261 2013-01-01T00:00:00.000Z 1.6344878E7 309.65742109052326 2.9305616E7 2080.8911324983264 2014-01-01T00:00:00.000Z 45642.0 23.168527918781727 2.9351258E7 1669.3466115824176

## Step 11. Performance Analysis

In [0]:

yearly_product_sales_df = (
    fact_df
    .filter(F.col("order_date").isNotNull())
    .join(prod_df, "product_key", "left")
    .groupBy(
        F.year("order_date").alias("order_year"),
        "product_name"
    )
    .agg(F.sum("sales_amount").alias("current_sales"))
)

In [0]:
w_product = Window.partitionBy("product_name")
w_product_time = Window.partitionBy("product_name").orderBy("order_year")


In [0]:
performance_df = (
    yearly_product_sales_df
    .withColumn("avg_sales", F.avg("current_sales").over(w_product))
    .withColumn("diff_avg", F.col("current_sales") - F.col("avg_sales"))
    .withColumn(
        "sales_status",
        F.when(F.col("diff_avg") > 0, "Above Avg")
         .when(F.col("diff_avg") < 0, "Below Avg")
         .otherwise("Avg")
    )
    .withColumn(
        "previous_year_sale",
        F.lag("current_sales").over(w_product_time)
    )
    .withColumn(
        "diff_previous_year",
        F.col("current_sales") - F.col("previous_year_sale")
    )
    .withColumn(
        "sales_status_previous_year",
        F.when(F.col("diff_previous_year") > 0, "Increased")
         .when(F.col("diff_previous_year") < 0, "Decreased")
         .otherwise("Same")
    )
    .orderBy("product_name", "order_year")
)
performance_df.display()

order_year product_name current_sales avg_sales diff_avg sales_status previous_year_sale diff_previous_year sales_status_previous_year 2012 AWC Logo Cap 72.0 6570.0 -6498.0 Below Avg null null Same 2013 AWC Logo Cap 18891.0 6570.0 12321.0 Above Avg 72.0 18819.0 Increased 2014 AWC Logo Cap 747.0 6570.0 -5823.0 Below Avg 18891.0 -18144.0 Decreased 2012 All-Purpose Bike Stand 159.0 13197.0 -13038.0 Below Avg null null Same 2013 All-Purpose Bike Stand 37683.0 13197.0 24486.0 Above Avg 159.0 37524.0 Increased 2014 All-Purpose Bike Stand 1749.0 13197.0 -11448.0 Below Avg 37683.0 -35934.0 Decreased 2013 Bike Wash - Dissolver 6960.0 3636.0 3324.0 Above Avg null null Same 2014 Bike Wash - Dissolver 312.0 3636.0 -3324.0 Below Avg 6960.0 -6648.0 Decreased 2013 Classic Vest- L 11968.0 6240.0 5728.0 Above Avg null null Same 2014 Classic Vest- L 512.0 6240.0 -5728.0 Below Avg 11968.0 -11456.0 Decreased 2013 Classic Vest- M 11840.0 6368.0 5472.0 Above Avg null null Same 2014 Classic Vest- M 896.0 6368.0 -5472.0 Below Avg 11840.0 -10944.0 Decreased 2012 Classic Vest- S 64.0 3648.0 -3584.0 Below Avg null null Same 2013 Classic Vest- S 10368.0 3648.0 6720.0 Above Avg 64.0 10304.0 Increased 2014 Classic Vest- S 512.0 3648.0 -3136.0 Below Avg 10368.0 -9856.0 Decreased 2012 Fender Set - Mountain 110.0 15554.0 -15444.0 Below Avg null null Same 2013 Fender Set - Mountain 44484.0 15554.0 28930.0 Above Avg 110.0 44374.0 Increased 2014 Fender Set - Mountain 2068.0 15554.0 -13486.0 Below Avg 44484.0 -42416.0 Decreased 2012 HL Mountain Tire 140.0 16286.666666666666 -16146.666666666666 Below Avg null null Same 2013 HL Mountain Tire 46935.0 16286.666666666666 30648.333333333336 Above Avg 140.0 46795.0 Increased 2014 HL Mountain Tire 1785.0 16286.666666666666 -14501.666666666666 Below Avg 46935.0 -45150.0 Decreased 2012 HL Road Tire 132.0 9438.0 -9306.0 Below Avg null null Same 2013 HL Road Tire 26532.0 9438.0 17094.0 Above Avg 132.0 26400.0 Increased 2014 HL Road Tire 1650.0 9438.0 -7788.0 Below Avg 26532.0 -24882.0 Decreased 2012 Half-Finger Gloves- L 24.0 3544.0 -3520.0 Below Avg null null Same 2013 Half-Finger Gloves- L 10248.0 3544.0 6704.0 Above Avg 24.0 10224.0 Increased 2014 Half-Finger Gloves- L 360.0 3544.0 -3184.0 Below Avg 10248.0 -9888.0 Decreased 2012 Half-Finger Gloves- M 24.0 3992.0 -3968.0 Below Avg null null Same 2013 Half-Finger Gloves- M 11376.0 3992.0 7384.0 Above Avg 24.0 11352.0 Increased 2014 Half-Finger Gloves- M 576.0 3992.0 -3416.0 Below Avg 11376.0 -10800.0 Decreased 2012 Half-Finger Gloves- S 24.0 3896.0 -3872.0 Below Avg null null Same 2013 Half-Finger Gloves- S 11064.0 3896.0 7168.0 Above Avg 24.0 11040.0 Increased 2014 Half-Finger Gloves- S 600.0 3896.0 -3296.0 Below Avg 11064.0 -10464.0 Decreased 2013 Hitch Rack - 4-Bike 36840.0 19620.0 17220.0 Above Avg null null Same 2014 Hitch Rack - 4-Bike 2400.0 19620.0 -17220.0 Below Avg 36840.0 -34440.0 Decreased 2012 Hydration Pack - 70 oz. 110.0 13438.333333333334 -13328.333333333334 Below Avg null null Same 2013 Hydration Pack - 70 oz. 38940.0 13438.333333333334 25501.666666666664 Above Avg 110.0 38830.0 Increased 2014 Hydration Pack - 70 oz. 1265.0 13438.333333333334 -12173.333333333334 Below Avg 38940.0 -37675.0 Decreased 2013 LL Mountain Tire 20125.0 10775.0 9350.0 Above Avg null null Same 2014 LL Mountain Tire 1425.0 10775.0 -9350.0 Below Avg 20125.0 -18700.0 Decreased 2012 LL Road Tire 105.0 7301.0 -7196.0 Below Avg null null Same 2013 LL Road Tire 20622.0 7301.0 13321.0 Above Avg 105.0 20517.0 Increased 2014 LL Road Tire 1176.0 7301.0 -6125.0 Below Avg 20622.0 -19446.0 Decreased 2012 Long-Sleeve Logo Jersey- L 150.0 7550.0 -7400.0 Below Avg null null Same 2013 Long-Sleeve Logo Jersey- L 21550.0 7550.0 14000.0 Above Avg 150.0 21400.0 Increased 2014 Long-Sleeve Logo Jersey- L 950.0 7550.0 -6600.0 Below Avg 21550.0 -20600.0 Decreased 2012 Long-Sleeve Logo Jersey- M 50.0 7366.666666666667 -7316.666666666667 Below Avg null null Same 2013 Long-Sleeve Logo Jersey- M 20850.0 7366.666

## Step 12. Part-to-Whole (Proportion) Analysis

Identify which product categories contribute most to total sales.

In [0]:
#Total sales by category
category_sales_df = (
    fact_df
    .join(prod_df, "product_key", "left")
    .groupBy("category")
    .agg(F.sum("sales_amount").alias("total_sales"))
)

In [0]:
#Overall sales (total across all categories)
w_all = Window.rowsBetween(Window.unboundedPreceding, Window.unboundedFollowing)

category_proportion_df = (
    category_sales_df
    .withColumn("overall_sales", F.sum("total_sales").over(w_all))
    .withColumn(
        "sales_percentage",
        F.round(
            (F.col("total_sales") / F.col("overall_sales")) * 100, 2
        )
    )
)
category_proportion_df.display()

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


category total_sales overall_sales sales_percentage Accessories 700262.0 2.935625E7 2.39 Clothing 339716.0 2.935625E7 1.16 Bikes 2.8316272E7 2.935625E7 96.46

In [0]:
#Formatted and ordered version
final_category_share_df = (
    category_proportion_df
    .withColumn(
        "sales_percentage_label",
        F.concat(F.col("sales_percentage"), F.lit("%"))
    )
    .orderBy(F.desc("total_sales"))
)
final_category_share_df.display()

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


category total_sales overall_sales sales_percentage sales_percentage_label Bikes 2.8316272E7 2.935625E7 96.46 96.46% Accessories 700262.0 2.935625E7 2.39 2.39% Clothing 339716.0 2.935625E7 1.16 1.16%

## Step 13. Data Segmentation

Segment products and customers for deeper insights.

In [0]:
# Segment products into cost ranges
product_segments_df = (
    prod_df
    .withColumn(
        "cost_range",
        F.when(F.col("product_cost") < 100, "Below 100")
         .when((F.col("product_cost") >= 100) & (F.col("product_cost") <= 500), "100-500")
         .when((F.col("product_cost") > 500) & (F.col("product_cost") <= 1000), "500-1000")
         .otherwise("Above 1000")
    )
)
product_segments_df.display()

product_key product_id product_number product_name category_id category sub_category maintenance product_cost product_line start_date cost_range 1 210 FR-R92B-58 HL Road Frame - Black- 58 CO_RF Components Road Frames Yes 0 Road 2003-07-01 Below 100 2 211 FR-R92R-58 HL Road Frame - Red- 58 CO_RF Components Road Frames Yes 0 Road 2003-07-01 Below 100 3 348 BK-M82B-38 Mountain-100 Black- 38 BI_MB Bikes Mountain Bikes Yes 1898 Mountain 2011-07-01 Above 1000 4 349 BK-M82B-42 Mountain-100 Black- 42 BI_MB Bikes Mountain Bikes Yes 1898 Mountain 2011-07-01 Above 1000 5 350 BK-M82B-44 Mountain-100 Black- 44 BI_MB Bikes Mountain Bikes Yes 1898 Mountain 2011-07-01 Above 1000 6 351 BK-M82B-48 Mountain-100 Black- 48 BI_MB Bikes Mountain Bikes Yes 1898 Mountain 2011-07-01 Above 1000 7 344 BK-M82S-38 Mountain-100 Silver- 38 BI_MB Bikes Mountain Bikes Yes 1912 Mountain 2011-07-01 Above 1000 8 345 BK-M82S-42 Mountain-100 Silver- 42 BI_MB Bikes Mountain Bikes Yes 1912 Mountain 2011-07-01 Above 1000 9 346 BK-M82S-44 Mountain-100 Silver- 44 BI_MB Bikes Mountain Bikes Yes 1912 Mountain 2011-07-01 Above 1000 10 347 BK-M82S-48 Mountain-100 Silver- 48 BI_MB Bikes Mountain Bikes Yes 1912 Mountain 2011-07-01 Above 1000 11 317 BK-R68R-44 Road-450 Red- 44 BI_RB Bikes Road Bikes Yes 885 Road 2011-07-01 500-1000 12 318 BK-R68R-48 Road-450 Red- 48 BI_RB Bikes Road Bikes Yes 885 Road 2011-07-01 500-1000 13 319 BK-R68R-52 Road-450 Red- 52 BI_RB Bikes Road Bikes Yes 885 Road 2011-07-01 500-1000 14 315 BK-R68R-58 Road-450 Red- 58 BI_RB Bikes Road Bikes Yes 885 Road 2011-07-01 500-1000 15 316 BK-R68R-60 Road-450 Red- 60 BI_RB Bikes Road Bikes Yes 885 Road 2011-07-01 500-1000 16 311 BK-R93R-44 Road-150 Red- 44 BI_RB Bikes Road Bikes Yes 2171 Road 2011-07-01 Above 1000 17 312 BK-R93R-48 Road-150 Red- 48 BI_RB Bikes Road Bikes Yes 2171 Road 2011-07-01 Above 1000 18 313 BK-R93R-52 Road-150 Red- 52 BI_RB Bikes Road Bikes Yes 2171 Road 2011-07-01 Above 1000 19 314 BK-R93R-56 Road-150 Red- 56 BI_RB Bikes Road Bikes Yes 2171 Road 2011-07-01 Above 1000 20 310 BK-R93R-62 Road-150 Red- 62 BI_RB Bikes Road Bikes Yes 2171 Road 2011-07-01 Above 1000 21 299 FR-M94B-44 HL Mountain Frame - Black- 44 CO_MF Components Mountain Frames Yes 699 Mountain 2011-07-01 500-1000 22 300 FR-M94B-48 HL Mountain Frame - Black- 48 CO_MF Components Mountain Frames Yes 699 Mountain 2011-07-01 500-1000 23 291 FR-M94S-44 HL Mountain Frame - Silver- 44 CO_MF Components Mountain Frames Yes 707 Mountain 2011-07-01 500-1000 24 292 FR-M94S-52 HL Mountain Frame - Silver- 48 CO_MF Components Mountain Frames Yes 707 Mountain 2011-07-01 500-1000 25 274 FR-R72R-44 ML Road Frame - Red- 44 CO_RF Components Road Frames Yes 352 Road 2011-07-01 100-500 26 275 FR-R72R-48 ML Road Frame - Red- 48 CO_RF Components Road Frames Yes 352 Road 2011-07-01 100-500 27 276 FR-R72R-52 ML Road Frame - Red- 52 CO_RF Components Road Frames Yes 352 Road 2011-07-01 100-500 28 277 FR-R72R-58 ML Road Frame - Red- 58 CO_RF Components Road Frames Yes 352 Road 2011-07-01 100-500 29 278 FR-R72R-60 ML Road Frame - Red- 60 CO_RF Components Road Frames Yes 352 Road 2011-07-01 100-500 30 219 SO-B909-L Mountain Bike Socks- L CL_SO Clothing Socks No 3 Mountain 2011-07-01 Below 100 31 218 SO-B909-M Mountain Bike Socks- M CL_SO Clothing Socks No 3 Mountain 2011-07-01 Below 100 32 364 BK-M47B-38 Mountain-300 Black- 38 BI_MB Bikes Mountain Bikes Yes 598 Mountain 2012-07-01 500-1000 33 365 BK-M47B-40 Mountain-300 Black- 40 BI_MB Bikes Mountain Bikes Yes 598 Mountain 2012-07-01 500-1000 34 366 BK-M47B-44 Mountain-300 Black- 44 BI_MB Bikes Mountain Bikes Yes 598 Mountain 2012-07-01 500-1000 35 367 BK-M47B-48 Mountain-300 Black- 48 BI_MB Bikes Mountain Bikes Yes 598 Mountain 2012-07-01 500-1000 36 339 BK-R50B-44 Road-650 Black- 44 BI_RB Bikes Road Bikes Yes 487 Road 2012-07-01 100-500 37 341 BK-R50B-48 Road-650 Black- 48 BI_RB Bikes Road Bikes Yes 487 Road 2012-07-01 100-500 38 343 BK-R50B-52 Road-650 Black- 52 BI_RB Bikes Road Bikes Yes 487 Road 2012-

In [0]:
# Count how many products fall into each cost segment
product_segment_counts_df = (
    product_segments_df
    .groupBy("cost_range")
    .agg(F.count("product_key").alias("total_products"))
    .orderBy(F.desc("total_products"))
)
product_segment_counts_df.display()

cost_range total_products Below 100 110 100-500 101 500-1000 45 Above 1000 39

In [0]:
# Calculate customer lifespan and total spending
customer_spending_df = (
    fact_df
    .join(cust_df, "customer_key", "left")
    .groupBy("customer_key")
    .agg(
        F.sum("sales_amount").alias("total_spending"),
        F.min("order_date").alias("first_order"),
        F.max("order_date").alias("last_order")
    )
    .withColumn(
        "lifespan",
        F.floor(F.months_between("last_order", "first_order"))
    )
)
customer_spending_df.display()

customer_key total_spending first_order last_order lifespan 17149 3578.0 2011-03-19 2011-03-19 0 3139 4443.0 2011-06-05 2013-06-03 23 15277 3362.0 2012-01-27 2013-11-18 21 4366 3142.0 2012-05-21 2013-08-15 14 2737 4479.0 2012-06-09 2013-12-19 18 5156 4490.0 2012-12-05 2013-11-18 11 16557 2049.0 2012-12-26 2012-12-26 0 2936 57.0 2013-03-02 2013-03-02 0 4885 40.0 2013-05-07 2013-05-07 0 3683 138.0 2013-05-17 2013-12-06 6 14397 2398.0 2013-06-28 2013-06-28 0 12451 578.0 2013-09-05 2013-09-05 0 1021 804.0 2013-10-12 2013-10-12 0 14322 1736.0 2013-10-18 2013-10-18 0 11451 799.0 2013-10-29 2013-10-29 0 12914 48.0 2013-12-30 2013-12-30 0 94 8180.0 2011-04-07 2013-06-08 26 8632 5279.0 2011-09-22 2013-06-03 20 10203 4633.0 2012-01-27 2013-08-27 19 4529 1676.0 2012-08-19 2013-11-30 15 13884 2487.0 2013-01-04 2013-01-04 0 10255 90.0 2013-02-11 2013-02-11 0 1721 50.0 2013-06-12 2013-06-12 0 6522 1751.0 2013-07-04 2013-07-04 0 18343 801.0 2013-08-11 2013-08-11 0 10288 45.0 2013-08-15 2013-08-15 0 12354 45.0 2013-09-30 2013-09-30 0 9339 124.0 2013-10-21 2013-10-21 0 12604 2373.0 2013-12-18 2013-12-18 0 5375 15.0 2013-12-20 2013-12-20 0 15830 1728.0 2013-12-24 2013-12-24 0 1257 5953.0 2011-03-30 2013-08-16 28 7219 6021.0 2011-05-11 2013-01-09 19 16054 783.0 2012-03-15 2012-03-15 0 1329 6792.0 2012-06-04 2013-03-21 9 9915 1926.0 2012-11-03 2013-10-13 11 16263 2049.0 2012-11-22 2012-11-22 0 4834 2611.0 2012-12-10 2013-05-03 4 17111 845.0 2013-03-12 2013-03-12 0 1007 144.0 2013-05-05 2013-07-29 2 4252 200.0 2013-05-06 2014-01-28 8 14408 2398.0 2013-06-09 2013-06-09 0 2332 66.0 2013-07-12 2013-07-12 0 11224 35.0 2013-09-27 2013-09-27 0 9326 79.0 2013-10-31 2013-10-31 0 10386 609.0 2013-12-18 2013-12-18 0 10618 15.0 2014-01-20 2014-01-20 0 17599 3578.0 2011-04-02 2011-04-02 0 991 8164.0 2011-11-13 2013-08-22 21 4017 1498.0 2011-12-05 2013-10-09 22 15576 2890.0 2012-05-10 2013-06-16 13 4172 4392.0 2012-09-30 2013-10-03 12 7072 69.0 2013-04-25 2013-04-25 0 9762 23.0 2013-05-17 2013-05-17 0 18444 89.0 2013-06-26 2013-06-26 0 9329 120.0 2013-08-18 2013-08-18 0 1983 58.0 2013-08-30 2013-10-03 1 1910 72.0 2013-10-18 2013-10-18 0 17193 30.0 2013-10-21 2013-10-21 0 4963 62.0 2013-11-23 2013-11-23 0 10082 21.0 2013-11-30 2013-11-30 0 8888 79.0 2013-12-18 2013-12-18 0 12714 35.0 2013-12-19 2013-12-19 0 14178 37.0 2014-01-25 2014-01-25 0 2515 5973.0 2011-02-17 2013-12-03 33 3326 5152.0 2012-09-24 2013-10-18 12 12942 39.0 2013-01-28 2013-01-28 0 14703 2419.0 2013-03-29 2013-03-29 0 9403 5.0 2013-06-16 2013-06-16 0 17716 589.0 2013-07-18 2013-07-18 0 13666 110.0 2013-07-31 2013-07-31 0 13555 70.0 2013-08-12 2013-08-12 0 13213 1155.0 2013-09-07 2013-09-07 0 11520 921.0 2013-10-31 2013-10-31 0 2744 2350.0 2013-11-07 2013-11-07 0 13011 565.0 2013-11-18 2013-11-18 0 7364 1701.0 2013-12-20 2013-12-20 0 29 6474.0 2011-01-26 2013-10-07 32 3586 3016.0 2011-03-26 2013-07-23 27 3611 1468.0 2011-04-05 2013-07-26 27 15644 699.0 2011-05-27 2011-05-27 0 10257 3918.0 2012-02-16 2013-10-21 20 5939 3110.0 2012-05-11 2013-12-24 19 5204 6940.0 2012-09-01 2013-10-18 13 3209 117.0 2013-02-05 2013-07-18 5 3810 115.0 2013-03-02 2013-08-02 5 7682 70.0 2013-03-24 2013-03-24 0 16247 29.0 2013-05-14 2013-05-14 0 14285 2419.0 2013-06-01 2013-06-01 0 17474 21.0 2013-09-17 2013-09-17 0 9787 15.0 2013-10-17 2013-10-17 0 13811 2419.0 2013-10-26 2013-10-26 0 9224 187.0 2013-11-05 2013-12-28 1 14767 33.0 2013-11-19 2013-11-19 0 18396 14.0 2013-12-05 2013-12-05 0 16303 36.0 2013-12-13 2013-12-13 0 7420 40.0 2014-01-16 2014-01-16 0 2543 5943.0 2011-02-26 2013-12-03 33 569 6789.0 2012-01-10 2013-09-20 20 16098 4464.0 2012-09-06 2013-09-02 11 2899 4835.0 2012-10-19 2013-06-10 7 13467 3337.0 2012-12-01 2013-06-04 6 15827 1238.0 2012-12-30 2012-12-30 0 6037 177.0 2013-02-20 2013-05-31 3 803 214.0 2013-02-25 2013-12-01 9 5441 29.0 2013-02-26 2013-02-26 0 3531 73.0 2013-03-20 2013-11-14 7 3712 72.0 2013-03-27 2013-03-27 0 4261 46.0 2013-04-04 2013-04-04 0 4573 105.0 2013-07-03 2013-10-14 3 9586 32.0 

In [0]:
# Segment customers based on spending and activity
#  Criteria:
#  - VIP: ≥12 months history and spending > $5000
#  - Regular: ≥12 months history and spending ≤ $5000
#  - New: <12 months history
# Assign customer segments based on lifespan and spending
customer_segments_df = (
    customer_spending_df
    .withColumn(
        "customer_segment",
        F.when((F.col("lifespan") >= 12) & (F.col("total_spending") > 5000), "VIP")
         .when((F.col("lifespan") >= 12) & (F.col("total_spending") <= 5000), "Regular")
         .otherwise("New")
    )
)
customer_segments_df.display()

customer_key total_spending first_order last_order lifespan customer_segment 17149 3578.0 2011-03-19 2011-03-19 0 New 3139 4443.0 2011-06-05 2013-06-03 23 Regular 15277 3362.0 2012-01-27 2013-11-18 21 Regular 4366 3142.0 2012-05-21 2013-08-15 14 Regular 2737 4479.0 2012-06-09 2013-12-19 18 Regular 5156 4490.0 2012-12-05 2013-11-18 11 New 16557 2049.0 2012-12-26 2012-12-26 0 New 2936 57.0 2013-03-02 2013-03-02 0 New 4885 40.0 2013-05-07 2013-05-07 0 New 3683 138.0 2013-05-17 2013-12-06 6 New 14397 2398.0 2013-06-28 2013-06-28 0 New 12451 578.0 2013-09-05 2013-09-05 0 New 1021 804.0 2013-10-12 2013-10-12 0 New 14322 1736.0 2013-10-18 2013-10-18 0 New 11451 799.0 2013-10-29 2013-10-29 0 New 12914 48.0 2013-12-30 2013-12-30 0 New 94 8180.0 2011-04-07 2013-06-08 26 VIP 8632 5279.0 2011-09-22 2013-06-03 20 VIP 10203 4633.0 2012-01-27 2013-08-27 19 Regular 4529 1676.0 2012-08-19 2013-11-30 15 Regular 13884 2487.0 2013-01-04 2013-01-04 0 New 10255 90.0 2013-02-11 2013-02-11 0 New 1721 50.0 2013-06-12 2013-06-12 0 New 6522 1751.0 2013-07-04 2013-07-04 0 New 18343 801.0 2013-08-11 2013-08-11 0 New 10288 45.0 2013-08-15 2013-08-15 0 New 12354 45.0 2013-09-30 2013-09-30 0 New 9339 124.0 2013-10-21 2013-10-21 0 New 12604 2373.0 2013-12-18 2013-12-18 0 New 5375 15.0 2013-12-20 2013-12-20 0 New 15830 1728.0 2013-12-24 2013-12-24 0 New 1257 5953.0 2011-03-30 2013-08-16 28 VIP 7219 6021.0 2011-05-11 2013-01-09 19 VIP 16054 783.0 2012-03-15 2012-03-15 0 New 1329 6792.0 2012-06-04 2013-03-21 9 New 9915 1926.0 2012-11-03 2013-10-13 11 New 16263 2049.0 2012-11-22 2012-11-22 0 New 4834 2611.0 2012-12-10 2013-05-03 4 New 17111 845.0 2013-03-12 2013-03-12 0 New 1007 144.0 2013-05-05 2013-07-29 2 New 4252 200.0 2013-05-06 2014-01-28 8 New 14408 2398.0 2013-06-09 2013-06-09 0 New 2332 66.0 2013-07-12 2013-07-12 0 New 11224 35.0 2013-09-27 2013-09-27 0 New 9326 79.0 2013-10-31 2013-10-31 0 New 10386 609.0 2013-12-18 2013-12-18 0 New 10618 15.0 2014-01-20 2014-01-20 0 New 17599 3578.0 2011-04-02 2011-04-02 0 New 991 8164.0 2011-11-13 2013-08-22 21 VIP 4017 1498.0 2011-12-05 2013-10-09 22 Regular 15576 2890.0 2012-05-10 2013-06-16 13 Regular 4172 4392.0 2012-09-30 2013-10-03 12 Regular 7072 69.0 2013-04-25 2013-04-25 0 New 9762 23.0 2013-05-17 2013-05-17 0 New 18444 89.0 2013-06-26 2013-06-26 0 New 9329 120.0 2013-08-18 2013-08-18 0 New 1983 58.0 2013-08-30 2013-10-03 1 New 1910 72.0 2013-10-18 2013-10-18 0 New 17193 30.0 2013-10-21 2013-10-21 0 New 4963 62.0 2013-11-23 2013-11-23 0 New 10082 21.0 2013-11-30 2013-11-30 0 New 8888 79.0 2013-12-18 2013-12-18 0 New 12714 35.0 2013-12-19 2013-12-19 0 New 14178 37.0 2014-01-25 2014-01-25 0 New 2515 5973.0 2011-02-17 2013-12-03 33 VIP 3326 5152.0 2012-09-24 2013-10-18 12 VIP 12942 39.0 2013-01-28 2013-01-28 0 New 14703 2419.0 2013-03-29 2013-03-29 0 New 9403 5.0 2013-06-16 2013-06-16 0 New 17716 589.0 2013-07-18 2013-07-18 0 New 13666 110.0 2013-07-31 2013-07-31 0 New 13555 70.0 2013-08-12 2013-08-12 0 New 13213 1155.0 2013-09-07 2013-09-07 0 New 11520 921.0 2013-10-31 2013-10-31 0 New 2744 2350.0 2013-11-07 2013-11-07 0 New 13011 565.0 2013-11-18 2013-11-18 0 New 7364 1701.0 2013-12-20 2013-12-20 0 New 29 6474.0 2011-01-26 2013-10-07 32 VIP 3586 3016.0 2011-03-26 2013-07-23 27 Regular 3611 1468.0 2011-04-05 2013-07-26 27 Regular 15644 699.0 2011-05-27 2011-05-27 0 New 10257 3918.0 2012-02-16 2013-10-21 20 Regular 5939 3110.0 2012-05-11 2013-12-24 19 Regular 5204 6940.0 2012-09-01 2013-10-18 13 VIP 3209 117.0 2013-02-05 2013-07-18 5 New 3810 115.0 2013-03-02 2013-08-02 5 New 7682 70.0 2013-03-24 2013-03-24 0 New 16247 29.0 2013-05-14 2013-05-14 0 New 14285 2419.0 2013-06-01 2013-06-01 0 New 17474 21.0 2013-09-17 2013-09-17 0 New 9787 15.0 2013-10-17 2013-10-17 0 New 13811 2419.0 2013-10-26 2013-10-26 0 New 9224 187.0 2013-11-05 2013-12-28 1 New 14767 33.0 2013-11-19 2013-11-19 0 New 18396 14.0 2013-12-05 2013-12-05 0 New 16303 36.0 2013-12-13 2013-12-13 0 New 7420 40.0 2014-01-16 2014-01-16 0 New 2543 5943.0 20

In [0]:
# Count customers per segment
customer_segment_counts_df = (
    customer_segments_df
    .groupBy("customer_segment")
    .agg(F.count("customer_key").alias("total_customers"))
    .orderBy(F.desc("total_customers"))
)
customer_segment_counts_df.display()

customer_segment total_customers New 14828 Regular 2037 VIP 1619

## Step 14. Customer report view
Aggregate once → create reusable view

### Customer Report (gold.report_customers)

#### Purpose
Consolidated customer analytics table used for reporting, dashboards, and segmentation.

Provides one row per customer with behavioral, monetary, and lifecycle KPIs.

---

#### Grain
**1 row = 1 customer**

---

#### Data Sources
- gold.fact_sales
- gold.dim_customers

---

#### Metrics

##### Core KPIs
| Column | Description |
|-------|-------------|
| total_orders | Distinct orders placed |
| total_sales | Total revenue generated |
| total_quantity | Total items purchased |
| total_products | Distinct products purchased |
| last_order_date | Most recent purchase |
| recency | Months since last order |
| lifespan | Months between first and last order |

---

##### Customer Attributes
| Column | Description |
|--------|-------------|
| customer_age | Age derived from birth date |
| age_group | Age bucket for reporting |

Buckets:
- Under 20
- 20–29
- 30–39
- 40–49
- 50+

---

##### Segmentation
| Segment | Rule |
|---------|------|
| VIP | lifespan ≥ 12 months AND sales > 5000 |
| Regular | lifespan ≥ 12 months AND sales ≤ 5000 |
| New | lifespan < 12 months |

---

##### Derived Ratios
| Column | Formula |
|----------|-----------|
| avg_order_value | total_sales / total_orders |
| avg_monthly_spend | total_sales / lifespan |

---

#### Typical Uses
- Customer lifetime value analysis
- Segmentation dashboards
- RFM-style scoring
- Marketing targeting
- Retention monitoring

---

#### Notes
- Age and recency calculated dynamically using current date
- months_between used for month calculations (Spark equivalent of DATEDIFF(MONTH))
- Can be saved as a physical table for BI tools


In [0]:
today = F.current_date()

customer_report = (
    fact_df.join(cust_df, "customer_key")
    .groupBy(
        "customer_key",
        "customer_number",
        "first_name",
        "last_name",
        "birth_date"
    )
    .agg(
        F.countDistinct("order_number").alias("total_orders"),
        F.sum("sales_amount").alias("total_sales"),
        F.sum("quantity").alias("total_quantity"),
        F.countDistinct("product_key").alias("total_products"),
        F.max("order_date").alias("last_order_date"),
        F.floor(F.months_between(F.max("order_date"), F.min("order_date"))).alias("lifespan")
    )
    .withColumn("customer_name", F.concat_ws(" ", "first_name", "last_name"))
    .withColumn("customer_age", F.floor(F.months_between(today, "birth_date") / 12))
    .withColumn("recency", F.floor(F.months_between(today, "last_order_date")))

    .withColumn(
        "customer_segment",
        F.when((F.col("lifespan") >= 12) & (F.col("total_sales") > 5000), "VIP")
         .when((F.col("lifespan") >= 12), "Regular")
         .otherwise("New")
    )

    .withColumn(
        "avg_order_value",
        F.col("total_sales") / F.col("total_orders")
    )

    .withColumn(
        "avg_monthly_spend",
        F.when(F.col("lifespan") == 0, F.col("total_sales"))
         .otherwise(F.col("total_sales") / F.col("lifespan"))
    )
)
(
    customer_report
        .write
        .format("delta")
        .mode("overwrite")
        .saveAsTable("gold.report_customers")
)

## Step 15. Product report view

In [0]:
product_report = (
    fact_df
    .filter(F.col("order_date").isNotNull())
    .join(prod_df, "product_key", "left")
    .groupBy(
        "product_key",
        "product_name",
        "category",
        "sub_category",
        "product_cost"
    )
    .agg(
        F.countDistinct("order_number").alias("total_orders"),
        F.countDistinct("customer_key").alias("total_customers"),
        F.sum("sales_amount").alias("total_sales"),
        F.sum("quantity").alias("total_quantity"),
        F.max("order_date").alias("last_sale_date"),

        F.floor(
            F.months_between(F.max("order_date"), F.min("order_date"))
        ).alias("lifespan"),

        F.round(
            F.avg(F.col("sales_amount") / F.when(F.col("quantity") == 0, None)
                                           .otherwise(F.col("quantity"))),
            1
        ).alias("avg_selling_price")
    )
    .withColumn(
        "recency_in_months",
        F.floor(F.months_between(today, "last_sale_date"))
    )
    .withColumn(
        "product_segment",
        F.when(F.col("total_sales") > 50000, "High-Performer")
         .when(F.col("total_sales") >= 10000, "Mid-Range")
         .otherwise("Low-Performer")
    )

    .withColumn(
        "avg_order_revenue",
        F.col("total_sales") / F.col("total_orders")
    )
    .withColumn(
        "avg_monthly_revenue",
        F.when(F.col("lifespan") == 0, F.col("total_sales"))
         .otherwise(F.col("total_sales") / F.col("lifespan"))
    )
)

(
    product_report
        .write
        .format("delta")
        .mode("overwrite")
        .saveAsTable("gold.report_products")
)